In [42]:
import os
import datetime as dt
import tempfile

import requests
import panel as pn
import pandas as pd
import numpy as np
import holoviews as hv
import hvplot.pandas
hvplot.extension("bokeh")

pn.config.theme = "dark"


def _read_csv(url, *args, **kwargs):
    response = requests.get(url)
    try:
        tmp = tempfile.TemporaryFile(delete=False)
        tmp.write(response.content)
        tmp.close()
        df = pd.read_csv(tmp.name, *args, **kwargs)
    except:
        raise
    finally:
        os.remove(tmp.name)
    return df


def get_series(**options):
    df = _read_csv(options["url"], index_col=0, compression=None)
    
    df.index = pd.to_datetime(df.index, utc=True).tz_convert(options["tz"])
    df = df.sort_index(ascending=True)
    return df[[options["column"]]].rename(columns={options["column"]: options["name"]})


def get_dataframe(**options):
    df = _read_csv(options["url"], index_col=0, compression=None)
    df.index = pd.to_datetime(df.index, utc=True).tz_convert(options["tz"])
    df = df.sort_index(ascending=True)
    return df


active_tools = []
backend_opts={"plot.toolbar.autohide": True}
height=350
width=750

def utc_to_local(utc_dt):
    return utc_dt.replace(tzinfo=dt.timezone.utc).astimezone(tz=None)

now = dt.datetime.now(dt.UTC)
default_range = (utc_to_local(now-dt.timedelta(days=7)), utc_to_local(now))
range_select = pn.widgets.DatetimeRangePicker(
    value=default_range
)

start_time = dt.datetime.now(dt.UTC) - dt.timedelta(days=365)
start_time

datetime.datetime(2023, 5, 30, 13, 38, 49, 159456, tzinfo=datetime.timezone.utc)

In [43]:
options = dict(
    url="https://raw.githubusercontent.com/ryanfobel/ontario-grid-data/main/data/clean/gridwatch.ca/hourly/summary.csv",
    tz="America/Toronto",
    column="",
)

df = get_dataframe(**options)
df = df[df.index > start_time]

In [44]:
plot_options = dict(
    value_label="MW",
    legend="bottom",
    title="Ontario grid supply and demand",
    height=height,
    width=width,
    stacked=False,    
    grid=True,
    # ylim=(0, None),
    # alpha=0.5,
    # hover=False,
)
columns = {
    "Power Generated (MW)": "generated",
    "Ontario Demand (MW)": "demand",
    "Imports (MW)": "imports",
    "Exports (MW)": "exports",
    "Net Import/Exports (MW)": "net (exports-imports)",
}
suply_demand = df[columns.keys()].rename(columns=columns).hvplot.line(**plot_options).apply.opts(active_tools=active_tools, backend_opts=backend_opts, xlim=range_select, framewise=True)

rxy = hv.streams.RangeX(source=suply_demand)

def update_widget(event):
    new_dates = tuple([pd.Timestamp(i).to_pydatetime() for i in event.new])
    if new_dates != range_select.value:
        range_select.value = new_dates
rxy.param.watch(update_widget, 'x_range')

suply_demand

Traceback (most recent call last):
 File "C:\Users\ryan\miniconda3\envs\pn\Lib\site-packages\pyviz_comms\__init__.py", line 340, in _handle_msg
 self._on_msg(msg)
 File "C:\Users\ryan\miniconda3\envs\pn\Lib\site-packages\panel\viewable.py", line 469, in _on_msg
 patch = manager.assemble(msg)
 ^^^^^^^^^^^^^^^^^^^^^
 File "C:\Users\ryan\miniconda3\envs\pn\Lib\site-packages\panel\models\comm_manager.py", line 29, in assemble
 msg_obj = cls(header, msg['metadata'], msg['content'])
 ~~~^^^^^^^^^^^
KeyError: 'content'
 


 Traceback (most recent call last):
 File "C:\Users\ryan\miniconda3\envs\pn\Lib\site-packages\pyviz_comms\__init__.py", line 340, in _handle_msg
 self._on_msg(msg)
 File "C:\Users\ryan\miniconda3\envs\pn\Lib\site-packages\panel\viewable.py", line 469, in _on_msg
 patch = manager.assemble(msg)
 ^^^^^^^^^^^^^^^^^^^^^
 File "C:\Users\ryan\miniconda3\envs\pn\Lib\site-packages\panel\models\comm_manager.py", line 29, in assemble
 msg_obj = cls(header, msg['metadata'], msg['content'])
 ~~~^^^^^^^^^^^
KeyError: 'content'
 


 Traceback (most recent call last):
 File "C:\Users\ryan\miniconda3\envs\pn\Lib\site-packages\pyviz_comms\__init__.py", line 340, in _handle_msg
 self._on_msg(msg)
 File "C:\Users\ryan\miniconda3\envs\pn\Lib\site-packages\panel\viewable.py", line 469, in _on_msg
 patch = manager.assemble(msg)
 ^^^^^^^^^^^^^^^^^^^^^
 File "C:\Users\ryan\miniconda3\envs\pn\Lib\site-packages\panel\models\comm_manager.py", line 29, in assemble
 msg_obj = cls(header, msg['metadata'], msg['content'])
 ~~~^^^^^^^^^^^
KeyError: 'content'
 


 Traceback (most recent call last):
 File "C:\Users\ryan\miniconda3\envs\pn\Lib\site-packages\pyviz_comms\__init__.py", line 340, in _handle_msg
 self._on_msg(msg)
 File "C:\Users\ryan\miniconda3\envs\pn\Lib\site-packages\panel\viewable.py", line 469, in _on_msg
 patch = manager.assemble(msg)
 ^^^^^^^^^^^^^^^^^^^^^
 File "C:\Users\ryan\miniconda3\envs\pn\Lib\site-packages\panel\models\comm_manager.py", line 29, in assemble
 msg_obj = cls(header, msg['metadata'], msg['content'])
 ~~~^^^^^^^^^^^
KeyError: 'content'

:DynamicMap   []
   :NdOverlay   [Variable]
      :Curve   [index]   (MW)

In [45]:
plot_options = dict(
    value_label="MW",
    legend="bottom",
    title="Ontario grid generation",
    height=height,
    width=width,
    grid=True,
    stacked=True,
    ylim=(0, None),
    alpha=0.5,
    hover=False,
)

columns = {x: x.replace(" (MW)", "") for x in df.columns if x.endswith(" (MW)") and (x[0]==x[0].lower())}
generation = df[columns.keys()].rename(columns=columns).hvplot.area(**plot_options).apply.opts(active_tools=active_tools, backend_opts=backend_opts, xlim=range_select.value)
generation

:NdOverlay   [Variable]
   :Area   [index]   (MW,Baseline)

In [46]:
plot_options = dict(
    value_label="%",
    legend="bottom",
    title="Ontario grid relative power mix (%)",
    height=height,
    width=width,
    grid=True,
    stacked=True,
    ylim=(0, 100),
    alpha=0.5,
    hover=False,
)

columns = {x: x.replace(" (%)", "") for x in df.columns if x.endswith(" (%)")}
generation_pct = df[columns.keys()].rename(columns=columns).hvplot.area(**plot_options).apply.opts(active_tools=active_tools, backend_opts=backend_opts, xlim=range_select.value)
generation_pct

:NdOverlay   [Variable]
   :Area   [index]   (%,Baseline)

In [47]:
options_gridwatch = dict(
    name = "gridwatch",
    url="https://raw.githubusercontent.com/ryanfobel/ontario-grid-data/main/data/clean/gridwatch.ca/hourly/summary.csv",
    tz="America/Toronto",
    column = "CO2e Intensity (g/kWh)"
)

options_co2signal = dict(
    name="co2signal",
    url="https://raw.githubusercontent.com/ryanfobel/ontario-grid-data/main/data/clean/co2signal.com/CA-ON/hourly/output.csv",
    column = "data.carbonIntensity",
    tz="America/Toronto",
)

df = get_series(**options_gridwatch).join(
    get_series(**options_co2signal),
    how="inner"
)

plot_options = dict(
    value_label="g/kWh",
    legend="bottom",
    title="Ontario grid co2 emissions intensity",
    height=height,
    width=width,
    grid=True,
    ylim=(0, None),
    # alpha=0.5,
    # hover=False,
)
df = df[df.index > start_time]
co2_intensity = df.hvplot.line(**plot_options).apply.opts(active_tools=active_tools, backend_opts=backend_opts, xlim=range_select.value)
co2_intensity

:NdOverlay   [Variable]
   :Curve   [index]   (g/kWh)

In [48]:
button_map = {
    "Last 12 hours": dt.timedelta(hours=12),
    "Last 24 hours": dt.timedelta(hours=24),
    "Last 2 days": dt.timedelta(days=2),
    "Last 7 days": dt.timedelta(days=7),
    "Last 30 days": dt.timedelta(days=30),
    "Last 90 days": dt.timedelta(days=90),
    "Last 6 months": dt.timedelta(days=365./2),
    "Last 1 year": dt.timedelta(days=365),
}

buttons = [
    pn.widgets.Button(name=name, button_type='light')
    for name in button_map.keys()
]

def b(event):
    now = dt.datetime.now(dt.UTC)
    delta = button_map[event.obj.name]
    new_dates = tuple([utc_to_local(now-delta), utc_to_local(now)])
    if new_dates != range_select.value:
        range_select.value = new_dates

for button in buttons:
    button.on_click(b)

template = pn.template.FastGridTemplate(
    row_height=200,
    theme_toggle=False,
    theme="dark",
    title="Ontario grid data",
    prevent_collision=False,
    sidebar=[range_select, *buttons],
    collapsed_sidebar=True,
)
template.main[0:2,0:6]=co2_intensity
template.main[0:2,6:12]=generation_pct
template.main[2:4,0:6]=suply_demand
template.main[2:4,6:12]=generation

In [49]:
template.servable();

In [11]:
#!panel convert index.ipynb --to pyodide-worker --out ..\docs --pwa --title "Ontario grid data"

Successfully converted index.ipynb to pyodide-worker target and wrote output to index.html.
Successfully wrote icons and images.
Successfully wrote site.manifest.
Successfully wrote serviceWorker.js.


http://localhost:8000/docs

In [10]:
#!python -m http.server